In [18]:
import tensorflow as tf
import numpy as np

In [62]:
def fcn_model_fn(features, labels, mode):
    """Model function for Fully connected NN."""
    # Input Layer
    input_layer = tf.reshape(features["x"], [-1, 784])

    
    dense_1 = tf.layers.dense(inputs=input_layer, units=200, activation=tf.nn.relu)
    #dropout_1 = tf.layers.dropout(
    #  inputs=dense_1, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

        
    # Logits Layer
    logits = tf.layers.dense(inputs=dense_1, units=10)
    predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }

    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

    # Calculate Loss (for both TRAIN and EVAL modes)
    loss = tf.losses.sparse_softmax_cross_entropy(labels, logits=logits)

    #accuracy_summary = tf.summary.scalar('accuracy', acc)
    # Configure the Training Op (for TRAIN mode)
    
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.005)
        train_op = optimizer.minimize(
            loss=loss,
            global_step=tf.train.get_global_step())
        acc, acc_update=tf.metrics.accuracy(labels=labels, predictions=predictions["classes"])
        logging_hook = tf.train.LoggingTensorHook({"loss" : loss, "accuracy" : acc_update}, every_n_iter=1)
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op, training_hooks=[logging_hook])

    # Add evaluation metrics (for EVAL mode)
    eval_metric_ops = {"accuracy": tf.metrics.accuracy(labels=labels, predictions=predictions["classes"])}
    return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)
    

In [3]:
'''
train_data = np.load("mnist_train_images.npy")
train_labels = np.load("mnist_train_labels.npy")
eval_data = np.load("mnist_test_images.npy")
eval_labels = np.load("mnist_test_labels.npy")
'''
mnist = tf.contrib.learn.datasets.load_dataset("mnist")
train_data = mnist.train.images # Returns np.array
train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
eval_data = mnist.test.images # Returns np.array
eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)


Extracting MNIST-data/train-images-idx3-ubyte.gz
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz


In [63]:
mnist_classifier = tf.estimator.Estimator(
    model_fn=fcn_model_fn, model_dir="mnist_fully_connected_model")


INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_task_type': 'worker', '_global_id_in_cluster': 0, '_is_chief': True, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f3ffacb3ad0>, '_evaluation_master': '', '_save_checkpoints_steps': None, '_keep_checkpoint_every_n_hours': 10000, '_service': None, '_num_ps_replicas': 0, '_tf_random_seed': None, '_master': '', '_num_worker_replicas': 1, '_task_id': 0, '_log_step_count_steps': 100, '_model_dir': 'mnist_fully_connected_model', '_save_summary_steps': 100}


In [10]:
tensors_to_log = ['loss', 'acc']
logging_hook = tf.train.LoggingTensorHook(tensors=tensors_to_log, every_n_iter=100)


In [64]:
with tf.device('/cpu:0'):
    train_input_fn = tf.estimator.inputs.numpy_input_fn(
        x={"x": train_data},
        y=train_labels,
        batch_size=64,
        num_epochs=100,
        shuffle=True)
    mnist_classifier.train(
        input_fn=train_input_fn)


INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from mnist_fully_connected_model/model.ckpt-111720
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 111721 into mnist_fully_connected_model/model.ckpt.
INFO:tensorflow:loss = 0.18790922, step = 111721
INFO:tensorflow:loss = 0.18790922, accuracy = 0.9375
INFO:tensorflow:loss = 0.24383552, accuracy = 0.9296875 (0.037 sec)
INFO:tensorflow:loss = 0.12750076, accuracy = 0.9427083 (0.004 sec)
INFO:tensorflow:loss = 0.17443065, accuracy = 0.94140625 (0.003 sec)
INFO:tensorflow:loss = 0.43513942, accuracy = 0.93125 (0.004 sec)
INFO:tensorflow:loss = 0.4556332, accuracy = 0.9166667 (0.004 sec)
INFO:tensorflow:loss = 0.18762109, accuracy = 0.91964287 (0.004 sec)
INFO:tensorflow:loss = 0.13625154, accuracy = 0.9277344 (0.003 sec)
INFO:te

INFO:tensorflow:loss = 0.07979657, accuracy = 0.9413377 (0.003 sec)
INFO:tensorflow:loss = 0.10737173, accuracy = 0.9414402 (0.002 sec)
INFO:tensorflow:loss = 0.092584796, accuracy = 0.94181037 (0.003 sec)
INFO:tensorflow:loss = 0.15453622, accuracy = 0.94190705 (0.003 sec)
INFO:tensorflow:loss = 0.21905026, accuracy = 0.9420021 (0.003 sec)
INFO:tensorflow:loss = 0.17249063, accuracy = 0.9420956 (0.003 sec)
INFO:tensorflow:loss = 0.049909417, accuracy = 0.94257814 (0.003 sec)
INFO:tensorflow:loss = 0.1308531, accuracy = 0.94279444 (0.003 sec)
INFO:tensorflow:loss = 0.37828243, accuracy = 0.9423668 (0.003 sec)
INFO:tensorflow:loss = 0.1047464, accuracy = 0.9425813 (0.002 sec)
INFO:tensorflow:loss = 0.32661945, accuracy = 0.94254035 (0.003 sec)
INFO:tensorflow:loss = 0.41814238, accuracy = 0.942125 (0.003 sec)
INFO:tensorflow:loss = 0.23402926, accuracy = 0.9418403 (0.003 sec)
INFO:tensorflow:loss = 0.44965625, accuracy = 0.94168305 (0.003 sec)
INFO:tensorflow:loss = 0.4077952, accuracy 

INFO:tensorflow:loss = 0.21203604, accuracy = 0.9437366 (0.003 sec)
INFO:tensorflow:loss = 0.23080578, accuracy = 0.94364315 (0.003 sec)
INFO:tensorflow:loss = 0.26698944, accuracy = 0.94375 (0.003 sec)
INFO:tensorflow:loss = 0.17982884, accuracy = 0.9437235 (0.003 sec)
INFO:tensorflow:loss = 0.18499044, accuracy = 0.9436973 (0.003 sec)
INFO:tensorflow:loss = 0.3057053, accuracy = 0.9435399 (0.002 sec)
INFO:tensorflow:loss = 0.16871431, accuracy = 0.9436454 (0.002 sec)
INFO:tensorflow:loss = 0.25300145, accuracy = 0.9435547 (0.002 sec)
INFO:tensorflow:loss = 0.11652802, accuracy = 0.9435944 (0.002 sec)
INFO:tensorflow:loss = 0.19511469, accuracy = 0.94350463 (0.002 sec)
INFO:tensorflow:loss = 0.15596768, accuracy = 0.9435442 (0.002 sec)
INFO:tensorflow:loss = 0.17320263, accuracy = 0.9435835 (0.002 sec)
INFO:tensorflow:loss = 0.30367354, accuracy = 0.9435587 (0.002 sec)
INFO:tensorflow:loss = 0.16307804, accuracy = 0.94359756 (0.002 sec)
INFO:tensorflow:loss = 0.21686855, accuracy = 0.

INFO:tensorflow:loss = 0.22802506, accuracy = 0.94229406 (0.003 sec)
INFO:tensorflow:loss = 0.17330107, accuracy = 0.9423247 (0.003 sec)
INFO:tensorflow:loss = 0.14878231, accuracy = 0.9423552 (0.003 sec)
INFO:tensorflow:loss = 0.20364198, accuracy = 0.94238555 (0.002 sec)
INFO:tensorflow:loss = 0.38128108, accuracy = 0.9421524 (0.003 sec)
INFO:tensorflow:loss = 0.20963193, accuracy = 0.9420956 (0.002 sec)
INFO:tensorflow:loss = 0.20768586, accuracy = 0.9421264 (0.002 sec)
INFO:tensorflow:loss = 0.12275252, accuracy = 0.94220054 (0.002 sec)
INFO:tensorflow:loss = 0.2514685, accuracy = 0.9421007 (0.002 sec)
INFO:tensorflow:loss = 0.05706145, accuracy = 0.9422611 (0.002 sec)
INFO:tensorflow:loss = 0.18961503, accuracy = 0.9421616 (0.002 sec)
INFO:tensorflow:loss = 0.14426881, accuracy = 0.9422349 (0.002 sec)
INFO:tensorflow:loss = 0.11758969, accuracy = 0.9423077 (0.002 sec)
INFO:tensorflow:loss = 0.13721398, accuracy = 0.94233733 (0.002 sec)
INFO:tensorflow:loss = 0.19162792, accuracy =

INFO:tensorflow:loss = 0.21243262, accuracy = 0.94221073 (0.002 sec)
INFO:tensorflow:loss = 0.33665782, accuracy = 0.94213456 (0.002 sec)
INFO:tensorflow:loss = 0.07685011, accuracy = 0.94225687 (0.002 sec)
INFO:tensorflow:loss = 0.11831363, accuracy = 0.9423128 (0.002 sec)
INFO:tensorflow:loss = 0.1423637, accuracy = 0.94230264 (0.003 sec)
INFO:tensorflow:loss = 0.20148294, accuracy = 0.9422926 (0.002 sec)
INFO:tensorflow:loss = 0.12911019, accuracy = 0.942348 (0.002 sec)
INFO:tensorflow:loss = 0.1911937, accuracy = 0.9423379 (0.002 sec)
INFO:tensorflow:loss = 0.24682102, accuracy = 0.94229513 (0.002 sec)
INFO:tensorflow:loss = 0.33454156, accuracy = 0.9421875 (0.002 sec)
INFO:tensorflow:loss = 0.18285146, accuracy = 0.94221026 (0.003 sec)
INFO:tensorflow:loss = 0.17905876, accuracy = 0.9422329 (0.002 sec)
INFO:tensorflow:loss = 0.25391278, accuracy = 0.9421907 (0.002 sec)
INFO:tensorflow:loss = 0.19454426, accuracy = 0.94214875 (0.002 sec)
INFO:tensorflow:loss = 0.16566983, accuracy 

...

INFO:tensorflow:loss = 0.07197115, accuracy = 0.968183 (0.002 sec)
INFO:tensorflow:loss = 0.03286855, accuracy = 0.96818334 (0.002 sec)
INFO:tensorflow:loss = 0.029204635, accuracy = 0.9681837 (0.003 sec)
INFO:tensorflow:loss = 0.060329616, accuracy = 0.96818393 (0.003 sec)
INFO:tensorflow:loss = 0.06930396, accuracy = 0.9681841 (0.002 sec)
INFO:tensorflow:loss = 0.032304674, accuracy = 0.9681845 (0.002 sec)
INFO:tensorflow:loss = 0.03600516, accuracy = 0.9681848 (0.002 sec)
INFO:tensorflow:loss = 0.075473815, accuracy = 0.968185 (0.002 sec)
INFO:tensorflow:loss = 0.13038425, accuracy = 0.968185 (0.002 sec)
INFO:tensorflow:loss = 0.04558167, accuracy = 0.9681854 (0.002 sec)
INFO:tensorflow:loss = 0.06558268, accuracy = 0.9681854 (0.002 sec)
INFO:tensorflow:loss = 0.076333225, accuracy = 0.9681854 (0.002 sec)
INFO:tensorflow:loss = 0.03025245, accuracy = 0.9681858 (0.002 sec)
INFO:tensorflow:loss = 0.034160968, accuracy = 0.96818614 (0.002 sec)
INFO:tensorflow:loss = 0.051012155, accura

INFO:tensorflow:loss = 0.1681903, accuracy = 0.96820056 (0.002 sec)
INFO:tensorflow:loss = 0.035505325, accuracy = 0.96820074 (0.002 sec)
INFO:tensorflow:loss = 0.04848297, accuracy = 0.9682009 (0.002 sec)
INFO:tensorflow:loss = 0.10140473, accuracy = 0.96820074 (0.002 sec)
INFO:tensorflow:loss = 0.05166519, accuracy = 0.96820074 (0.003 sec)
INFO:tensorflow:loss = 0.04600144, accuracy = 0.96820074 (0.002 sec)
INFO:tensorflow:loss = 0.10254167, accuracy = 0.9682008 (0.002 sec)
INFO:tensorflow:loss = 0.04250359, accuracy = 0.96820116 (0.002 sec)
INFO:tensorflow:loss = 0.06594104, accuracy = 0.96820134 (0.002 sec)
INFO:tensorflow:loss = 0.049729727, accuracy = 0.9682015 (0.002 sec)
INFO:tensorflow:loss = 0.08786433, accuracy = 0.9682017 (0.002 sec)
INFO:tensorflow:loss = 0.057495553, accuracy = 0.9682019 (0.002 sec)
INFO:tensorflow:loss = 0.054131873, accuracy = 0.9682021 (0.002 sec)
INFO:tensorflow:loss = 0.058735922, accuracy = 0.9682023 (0.002 sec)
INFO:tensorflow:loss = 0.08577896, ac

INFO:tensorflow:loss = 0.015161104, accuracy = 0.9682133 (0.002 sec)
INFO:tensorflow:loss = 0.09386139, accuracy = 0.9682134 (0.003 sec)
INFO:tensorflow:loss = 0.05049183, accuracy = 0.96821356 (0.003 sec)
INFO:tensorflow:loss = 0.03920628, accuracy = 0.96821374 (0.002 sec)
INFO:tensorflow:loss = 0.040311232, accuracy = 0.9682141 (0.003 sec)
INFO:tensorflow:loss = 0.08245235, accuracy = 0.9682143 (0.002 sec)
INFO:tensorflow:loss = 0.09035143, accuracy = 0.9682143 (0.002 sec)
INFO:tensorflow:loss = 0.1365774, accuracy = 0.9682141 (0.002 sec)
INFO:tensorflow:loss = 0.041110594, accuracy = 0.96821433 (0.002 sec)
INFO:tensorflow:loss = 0.11634228, accuracy = 0.96821433 (0.002 sec)
INFO:tensorflow:loss = 0.12870562, accuracy = 0.96821415 (0.002 sec)
INFO:tensorflow:loss = 0.05832343, accuracy = 0.96821433 (0.002 sec)
INFO:tensorflow:loss = 0.07690318, accuracy = 0.9682145 (0.002 sec)
INFO:tensorflow:loss = 0.0682729, accuracy = 0.9682147 (0.002 sec)
INFO:tensorflow:global_step/sec: 419.562


INFO:tensorflow:loss = 0.028489474, accuracy = 0.9682343 (0.002 sec)
INFO:tensorflow:loss = 0.11605626, accuracy = 0.9682345 (0.002 sec)
INFO:tensorflow:loss = 0.02628531, accuracy = 0.96823484 (0.002 sec)
INFO:tensorflow:loss = 0.041322082, accuracy = 0.9682352 (0.003 sec)
INFO:tensorflow:loss = 0.036494114, accuracy = 0.96823543 (0.002 sec)
INFO:tensorflow:loss = 0.02191285, accuracy = 0.9682358 (0.002 sec)
INFO:tensorflow:loss = 0.07083955, accuracy = 0.9682358 (0.002 sec)
INFO:tensorflow:loss = 0.039762452, accuracy = 0.96823615 (0.002 sec)
INFO:tensorflow:loss = 0.13783681, accuracy = 0.96823615 (0.002 sec)
INFO:tensorflow:loss = 0.049457062, accuracy = 0.9682363 (0.002 sec)
INFO:tensorflow:loss = 0.05003417, accuracy = 0.9682363 (0.002 sec)
INFO:tensorflow:loss = 0.12150243, accuracy = 0.9682364 (0.002 sec)
INFO:tensorflow:loss = 0.015042815, accuracy = 0.96823674 (0.002 sec)
INFO:tensorflow:loss = 0.063544355, accuracy = 0.96823657 (0.002 sec)
INFO:tensorflow:loss = 0.081270486,

INFO:tensorflow:loss = 0.036627226, accuracy = 0.96825427 (0.002 sec)
INFO:tensorflow:loss = 0.061105266, accuracy = 0.96825445 (0.002 sec)
INFO:tensorflow:loss = 0.062790334, accuracy = 0.96825445 (0.002 sec)
INFO:tensorflow:loss = 0.013715152, accuracy = 0.96825486 (0.002 sec)
INFO:tensorflow:loss = 0.05416155, accuracy = 0.96825486 (0.002 sec)
INFO:tensorflow:loss = 0.04118447, accuracy = 0.9682552 (0.002 sec)
INFO:tensorflow:loss = 0.025168203, accuracy = 0.9682556 (0.002 sec)
INFO:tensorflow:loss = 0.06399803, accuracy = 0.96825576 (0.002 sec)
INFO:tensorflow:loss = 0.074356146, accuracy = 0.96825594 (0.002 sec)
INFO:tensorflow:loss = 0.0355687, accuracy = 0.9682561 (0.002 sec)
INFO:tensorflow:loss = 0.018065166, accuracy = 0.96825653 (0.002 sec)
INFO:tensorflow:loss = 0.059106614, accuracy = 0.9682569 (0.002 sec)
INFO:tensorflow:loss = 0.01816075, accuracy = 0.96825725 (0.002 sec)
INFO:tensorflow:loss = 0.051374726, accuracy = 0.96825725 (0.002 sec)
INFO:tensorflow:loss = 0.10869

In [61]:
eval_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": eval_data},
    y=eval_labels,
    num_epochs=1,
    shuffle=False)
eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
print(eval_results)


INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-03-23-15:45:21
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from mnist_fully_connected_model/model.ckpt-111720
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-03-23-15:45:21
INFO:tensorflow:Saving dict for global step 111720: accuracy = 0.9437, global_step = 111720, loss = 0.19933249
{'loss': 0.19933249, 'global_step': 111720, 'accuracy': 0.9437}


In [78]:
def init_weights(shape):
    return tf.Variable(tf.random_normal(shape, stddev=0.01))

def init_bias(shape):
    return tf.Variable(tf.ones(shape))

In [76]:
params=(2,300,0.8,64,15000)

num_hidden_layers, hidden_layer_size, learning_rate, minibatch_size, epoch = params

input_layer_size=784
output_layer_size=10

x = tf.placeholder(tf.float32, [None, input_layer_size])
in_size, out_size = input_layer_size, hidden_layer_size

weights={}
biases={}
hidden_activations={}
in_value=x

for i in np.arange(1, num_hidden_layers+1):
    weights["W"+str(i)]=init_weights([in_size, out_size])
    biases["b"+str(i)]=init_bias([out_size])
    in_size, out_size = out_size, int(out_size*0.5)
    hidden_activations["h"+str(i)]=tf.nn.relu(tf.matmul(in_value, graph.get_tensor_by_name("W1")) + graph.get_tensor_by_name("b1"))
    

In [77]:
weights

{'W1': <tf.Variable 'W1_8:0' shape=(784, 300) dtype=float32_ref>,
 'W2': <tf.Variable 'W1_9:0' shape=(300, 150) dtype=float32_ref>}